# Mapping Peaks in the Bristish Isles

This notebook plots all the peaks in the British Isles that might be considered Munros or equivalent (greater than 1000ft) using OSM ([OpenStreetMap](https://www.openstreetmap.org/#map=6/53.645/-3.911&layers=Y])) data. The OSM data is also compared with [SRTM data from NASA](https://www.usgs.gov/centers/eros/science/usgs-eros-archive-digital-elevation-shuttle-radar-topography-mission-srtm-1-arc?qt-science_center_objects=0#qt-science_center_objects) and the DoBIH ([Database of British and Irish Hills](http://www.hills-database.co.uk/downloads.html)). In doing so we can see some significant discrepencies, with a substatial number of elevations needing correcting in OSM. There are also quite a few peaks in OSM that are not in the DoBIH.

In [1]:
## import libraries

# note to use xarray's open_rasterio function GDAL & Rasterio also need installing
# See https://rasterio.readthedocs.io/en/latest/installation.html#windows

import requests
import json

import openstreetmap_mapping as osm

import pandas as pd
import xarray as xr 

from scipy import spatial

from bokeh.plotting import show, output_file
from bokeh.io import output_notebook
from bokeh.models import OpenURL, TapTool

output_notebook()

Loading BokehJS ...

In [2]:
## Import libraries

# To use xarray's open_rasterio function GDAL & Rasterio also need installing, see https://rasterio.readthedocs.io/en/latest/installation.html#windows

import requests
import json

from scipy import spatial

from types import SimpleNamespace

import openstreetmap_mapping as osm

import pandas as pd

import xarray as xr 



from bokeh.plotting import show, output_file
from bokeh.io import output_notebook
from bokeh.models import OpenURL, TapTool
output_notebook()

# Comparison height data from http://www.hills-database.co.uk/downloads.html
# Attribution: The Database of British and Irish Hills v17.2
# License: Creative Commons License 4.0 International Licence.

Loading BokehJS ...

In [3]:
# make libraries auto-reload to make debugging and development easier
%load_ext autoreload
%autoreload 2

In [4]:
# create a Tag class to more easily identify and select the OSM tags
class Tags(object):
    
    def __init__(self, *initial_data, **kwargs):
              
        for dictionary in initial_data:
            
            for key in dictionary:

                if isinstance(dictionary[key], dict):
                    if len(dictionary[key])>1:
                        setattr(self, 'value', key)
                        setattr(self, key, Tags(dictionary[key]))
                    else:
                        setattr(self, key, Tags(dictionary[key]))
                else:
                    setattr(self, key, dictionary[key])
            
    def __repr__(self):
        return self.value.replace("__",":")
    
    def __str__(self):
        return self.value.replace("__",":")

In [5]:
# get the osm key-value pairs
kvs = osm.toolkit.get_osm_kvs()

In [6]:
# turn the key-value pairs into the tags class for use
tags = Tags(kvs)

In [7]:
# define rectangular areas for downloading osm data from
area_BritishIsles = "(48.327, -12.063, 61.428, 1.78)"
area_IsleOfMann = "(54, -5, 54.5, -4.2)"
area_NorthernIreland = "(53.924, -8.339, 55.417, -5.477)"

In [8]:
# get all the peak data from the specified area
df_mountains = osm.toolkit.get_osm_data(key=tags.natural,tag=tags.natural.peak,area=area_BritishIsles)

In [9]:
# copy the peak data to a "munros" dataframe that just considers peaks greater than 1000ft

df_munros = df_mountains.copy()

df_munros = df_munros[['id','name','lat','lon','tags','ele','source:ele','tag','key']]

df_munros['ele'] = pd.to_numeric(df_munros['ele'],errors='coerce')

df_munros = df_munros.dropna(subset = ['ele'])

df_munros['ele_ft'] = (df_munros['ele']*3.282).astype(int)

df_munros = df_munros[df_munros['ele_ft']>1000]

df_munros = df_munros.sort_values(by=['ele_ft'])

df_munros['osm_link'] = r'https://www.openstreetmap.org/node/'+df_munros['id'].astype(str)

df_munros['coordinate'] = list(zip(df_munros['lat'],df_munros['lon']))

In [10]:
# access the SRTM data downloaded and exported using QGIS 
# see https://www.geodose.com/2018/02/how-to-download-srtm-elevation-data-qgis.html

da = xr.open_rasterio("data/BritishIslesSRTM.tif")

In [11]:
# extract SRTM heights at the coordinates of the peaks
da_lons = xr.DataArray(df_munros['lon'], dims='munros')
da_lats = xr.DataArray(df_munros['lat'], dims='munros')
da_pathZIP = da.interp(y=da_lats, x=da_lons)

In [12]:
# add this data to the munros dataframe
df_munros['SRTM_height'] = list(da_pathZIP.values[0])

In [13]:
# read in the Database of British and Irish Hills data set
# accessible under the Creative Commons Attribution 4.0 International Licence
# see http://www.hills-database.co.uk/downloads.html

df_DoBIH = pd.read_csv('data/DoBIH_v17_2.csv',low_memory=False)

df_DoBIH = df_DoBIH[['Name','Feature','Metres','Latitude','Longitude']]

df_DoBIH['Coordinate'] = list(zip(df_DoBIH['Latitude'],df_DoBIH['Longitude']))

In [14]:
# combine the datasets based on the coordinates (closest located peaks)
# this is not 100% accurate, so when making any changes, the names need checking too!

tree = spatial.KDTree(list(df_DoBIH['Coordinate']))

distance,index = tree.query(list(df_munros['coordinate']))

df_munros['DoBIH_index'] = index
df_DoBIH['DoBIH_index'] = df_DoBIH.index

df_munros = pd.merge(df_munros, df_DoBIH, on="DoBIH_index")

In [15]:
# compare the elevations
df_munros['SRTM_height_diff'] = abs(df_munros['ele']-df_munros['SRTM_height'])
df_munros['DoBIH_height_diff'] = abs(df_munros['ele']-df_munros['Metres'])

In [16]:
# define plot legends
df_munros['legend'] = 'OSM height within 50m tolerance'
df_munros.loc[df_munros['SRTM_height_diff']>50,'legend'] = 'OSM-SRTM delta >50m'
df_munros.loc[df_munros['DoBIH_height_diff']>50,'legend'] = 'OSM-DoBIH delta >50m'
df_munros.loc[(df_munros['SRTM_height_diff']>50) & (df_munros['DoBIH_height_diff']>50),'legend'] = 'Both DoBIH & SRTM deltas >50m'

In [17]:
# define plot colors
df_munros['fill_color'] = 'white'
df_munros['line_color'] = 'black'

df_munros.loc[df_munros['SRTM_height_diff']>50,'fill_color'] = 'red'
df_munros.loc[df_munros['DoBIH_height_diff']>50,'line_color'] = 'red'

In [18]:
# create the plot

output_file("BritishIsles_Munros.html")

kwargs_for_figure = {"tooltips":[
                        ("name", "@name"),
                        ("DoBHI name", "@Name"),
                        ("Url", "@osm_link"),
                        ("OSM height [m]", "@ele"),
                        ("DoBHI height [m]", "@Metres"),
                        ("SRTM height [m]", "@SRTM_height"),
                        ("(lat,lon)", "@coordinates"),
                        ("DoBHI (lat,lon)", "@Coordinate")],
                     "sizing_mode":"scale_width",}

kwargs_for_marker={"marker":"triangle",
                   "fill_color":"fill_color",
                   "line_color":"line_color",
                   "legend_group":"legend"}

p = osm.toolkit.plot_latlon(df_munros,marker_size=10,kwargs_for_figure=kwargs_for_figure,kwargs_for_marker=kwargs_for_marker)

p.legend.background_fill_color = "lightcyan"
p.legend.click_policy="hide"

url = "@osm_link"
taptool = p.select(type=TapTool)
taptool.callback = OpenURL(url=url)

p.title = 'Peaks in the British Isles'

In [19]:
show(p)